In [131]:
!pip install trimesh numpy pandas

Defaulting to user installation because normal site-packages is not writeable



[notice] A new release of pip is available: 25.0.1 -> 25.1.1
[notice] To update, run: C:\Users\juanc\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.13_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip


# 1. Imports y configuración inicial

In [139]:
import trimesh
import numpy as np
import os
import pandas as pd

# 2. Función para cargar un modelo

In [81]:
import trimesh

def load_mesh(path: str) -> trimesh.Trimesh:
    """
    Carga un modelo 3D (.obj, .stl, .gltf, etc.) y devuelve un objeto Trimesh.
    """
    mesh = trimesh.load(path, force='mesh')
    if not isinstance(mesh, trimesh.Trimesh):
        # si es Scene, convertimos a un único mesh
        mesh = trimesh.util.concatenate(mesh.dump())
    return mesh
mesh_obj  = load_mesh('Datos/ElectricScooter.obj')
mesh_stl  = load_mesh('Datos/ElectricScooter.stl')
mesh_gltf = load_mesh('Datos/ElectricScooter.gltf')

# 3. Función de comparación de propiedades

In [99]:
def mesh_summary(mesh: trimesh.Trimesh) -> dict:
    n_vertices = len(mesh.vertices)
    n_faces    = len(mesh.faces)
    has_normals = mesh.vertex_normals is not None and len(mesh.vertex_normals) == n_vertices
    return {
        'vertices': n_vertices,
        'faces':    n_faces,
        'normals':  has_normals
    }




def count_duplicate_vertices(mesh: trimesh.Trimesh, tol=1e-8) -> int:
    """
    Cuenta vértices duplicados dentro de una tolerancia tol.
    """
    verts = mesh.vertices
    # redondeamos para agrupar
    rounded = np.round(verts / tol).astype(np.int64)
    # contamos ocurrencias
    uniq, counts = np.unique(rounded, axis=0, return_counts=True)
    duplicates = counts[counts > 1].sum() - len(counts[counts > 1])
    return int(duplicates)



# 4. Función de visualización

In [100]:
print(mesh_summary(mesh_obj))
print("Dup. vértices:", count_duplicate_vertices(mesh_obj))
mesh_obj.show()  # abre ventana externa con pyglet


{'vertices': 2434, 'faces': 2356, 'normals': True}
Dup. vértices: 1195


In [101]:
print(mesh_summary(mesh_stl))
print("Dup. vértices:", count_duplicate_vertices(mesh_stl))
mesh_stl.show()  # abre ventana externa con pyglet

{'vertices': 1249, 'faces': 2356, 'normals': True}
Dup. vértices: 0


In [102]:
print(mesh_summary(mesh_gltf))
print("Dup. vértices:", count_duplicate_vertices(mesh_gltf))
mesh_gltf.show()  # abre ventana externa con pyglet

{'vertices': 2479, 'faces': 2356, 'normals': True}
Dup. vértices: 1240


# 5. Función de conversión de formato

In [146]:
from pathlib import Path
import trimesh

def convert_format(mesh: trimesh.Trimesh, out_path: str):
    """
    Guarda `mesh` en el formato indicado por la extensión de `out_path`.
    Usa mesh.export(), que detecta el tipo automáticamente.
    """
    out = Path(out_path)
    # Asegurarnos de que la carpeta existe
    out.parent.mkdir(parents=True, exist_ok=True)
    # mesh.export reconoce la extensión y devuelve bytes o texto
    data = mesh.export(file_type=out.suffix.lower().lstrip('.'))
    # Si data es string, lo codificamos a UTF-8
    mode = 'wb' if isinstance(data, (bytes, bytearray)) else 'w'
    with open(out, mode) as f:
        f.write(data)
    print(f"Convertido y guardado en {out_path}")


convert_format(mesh_obj, 'Resultados/modelo_convertido(OBJ-STL).stl')
convert_format(mesh_obj, 'Resultados/modelo_convertido(OBJ-GLB).glb')
convert_format(mesh_stl, 'Resultados/modelo_convertido(STL-OBJ).obj')
convert_format(mesh_stl, 'Resultados/modelo_convertido(STL-GLB).glb')
convert_format(mesh_gltf, 'Resultados/modelo_convertido(GLTF-OBJ).obj')
convert_format(mesh_gltf, 'Resultados/modelo_convertido(GLTF-STL).stl')

Convertido y guardado en Resultados/modelo_convertido(OBJ-STL).stl
Convertido y guardado en Resultados/modelo_convertido(OBJ-GLB).glb
Convertido y guardado en Resultados/modelo_convertido(STL-OBJ).obj
Convertido y guardado en Resultados/modelo_convertido(STL-GLB).glb
Convertido y guardado en Resultados/modelo_convertido(GLTF-OBJ).obj
Convertido y guardado en Resultados/modelo_convertido(GLTF-STL).stl


In [147]:
mesh_cambio = load_mesh('Resultados/modelo_convertido(OBJ-STL).stl')
print(mesh_summary(mesh_cambio))
print("Dup. vértices:", count_duplicate_vertices(mesh_cambio))
mesh_cambio.show()  # abre ventana externa con pyglet

{'vertices': 1239, 'faces': 2356, 'normals': True}
Dup. vértices: 0


# 6. Automatizar comparación de múltiples modelos en un directorio

In [142]:
def batch_compare(directory: str) -> pd.DataFrame:
    """
    Recorre todos los archivos 3D de directory, carga y resume propiedades.
    Retorna un DataFrame con los resultados.
    """
    records = []
    for fname in os.listdir(directory):
        if fname.lower().endswith(('.obj', '.stl', '.gltf', '.glb', '.ply')):
            path = os.path.join(directory, fname)
            mesh = load_mesh(path)
            summary = mesh_summary(mesh)
            summary['duplicates'] = count_duplicate_vertices(mesh)
            summary['file'] = fname
            records.append(summary)
    df = pd.DataFrame(records)
    return df

# En tu notebook
df = batch_compare('Datos')
df  # muestra la tabla con vertices, caras, normales, duplicados por archivo


vertices  faces  normals  duplicates                  file
0      2479   2356     True        1240   ElectricScooter.glb
1      2479   2356     True        1240  ElectricScooter.gltf
2      2434   2356     True        1195   ElectricScooter.obj
3      1249   2356     True           0   ElectricScooter.STL

In [148]:
df = batch_compare('Resultados')
df

vertices  faces  normals  duplicates                             file
0      2438   2356     True        1199  modelo_convertido(GLTF-OBJ).obj
1      1239   2356     True           0  modelo_convertido(GLTF-STL).stl
2      2434   2356     True        1195   modelo_convertido(OBJ-GLB).glb
3      1239   2356     True           0   modelo_convertido(OBJ-STL).stl
4      1249   2356     True           0   modelo_convertido(STL-GLB).glb
5      1249   2356     True           0   modelo_convertido(STL-OBJ).obj